# 定义实体类

In [3]:
# 国外疫情实时概况
def OutsideSummary(dsin):
    class OutsideSummary:
        def __init__(self):
            self.currentConfirmedCount = 0
            self.confirmedCount = 0
            self.suspectedCount = 0
            self.curedCount = 0
            self.deadCount = 0
            self.suspectedIncr = 0
            self.currentConfirmedIncr = 0
            self.confirmedIncr = 0
            self.curedIncr = 0
            self.deadIncr = 0
            self.updatedTime = datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S')


        def get_info_tuple(self):
            return (self.currentConfirmedCount, self.confirmedCount, self.suspectedCount, self.curedCount,
                     self.deadCount, self.suspectedIncr, self.currentConfirmedIncr, self.confirmedIncr, self.curedIncr,
                     self.deadIncr, self.updatedTime)


        def __str__(self):
            return 'currentConfirmedCount:%s, confirmedCount:%s, suspectedCount:%s, curedCount:%s, deadCount:%s, suspectedIncr:%s, currentConfirmedIncr:%s, confirmedIncr:%s, curedIncr:%s, deadIncr:%s, updatedTime:%s' % (
            self.currentConfirmedCount, self.confirmedCount, self.suspectedCount, self.curedCount, self.deadCount,
            self.suspectedIncr, self.currentConfirmedIncr, self.confirmedIncr, self.curedIncr, self.deadIncr, self.updatedTime)

    # 数据库实体类

    #数据库实体类
    import pymysql
    class MyDB:
        def __init__(self, host, user, passwd, db):
            self.conn = pymysql.connect(host, user, passwd, db)
            self.cursor = self.conn.cursor()


        def get_outsideSummary_list_tuple(self, outsideSummary):
            info_tuple = []
            info_tuple.append(outsideSummary.get_info_tuple())
            return info_tuple


        # 保存数据
        def save_outsideSummary_datas(self, outsideSummary):
            print('+++ [MyDB] delete from outsideSummary_realtime_datas') 
            self.cursor.execute('delete from outsideSummary_realtime_datas') 
            self.conn.commit()

            sql = 'insert into outsideSummary_realtime_datas(currentConfirmedCount,confirmedCount,suspectedCount,curedCount,deadCount,suspectedIncr,currentConfirmedIncr,confirmedIncr,curedIncr,deadIncr,updatedTime) values(%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s)'
            res = self.get_outsideSummary_list_tuple(outsideSummary)
            print('+++ save_outsideSummary_datas, data len: %d' % len(res))
            try:
                self.cursor.executemany(sql, res)
                self.conn.commit()
            except Exception as e:
                print(e)
            print('+++ save_outsideSummary_datas is over.')


        def __del__(self):
            if self.conn is not None:
                self.conn.close()

    # 业务逻辑类

    #业务逻辑类
    import datetime
    import requests
    import re
    from bs4 import BeautifulSoup
    import json



    class DataService:
        def __init__(self,ds):
            self.db = MyDB(host = ds[0],user = ds[1],passwd = ds[2],db = ds[3])


    # 爬取页面
    res = requests.get('https://ncov.dxy.cn/ncovh5/view/pneumonia')

    # 重新解码
    res = res.content.decode('utf-8')

    # 构建soup对象
    soup = BeautifulSoup(res, 'html.parser')

    # 使用soup对象查找国外疫情数据标签
    tag = soup.find('script', attrs={'id': 'getStatisticsService'})

    # 转成字符串
    tagstr = tag.string
    # 使用正则表达式查找所有内容
    result = re.findall('\{"currentConfirmedCount".*?"deadIncr".*?\}', tagstr)

    # 获取国外疫情数据
    #print(result[0])
    obj = json.loads(result[0])



    #print(obj)
    def fetch_outside_summary(obj):
        outsideSummary = OutsideSummary()
        outsideSummary.currentConfirmedCount = int(obj['currentConfirmedCount'])
        outsideSummary.confirmedCount = int(obj['confirmedCount'])
        outsideSummary.suspectedCount = int(obj['suspectedCount'])
        outsideSummary.curedCount = int(obj['curedCount'])
        outsideSummary.deadCount = int(obj['deadCount'])
        outsideSummary.suspectedIncr = int(obj['suspectedIncr'])
        outsideSummary.currentConfirmedIncr = int(obj['currentConfirmedIncr'])
        outsideSummary.confirmedIncr = int(obj['confirmedIncr'])
        outsideSummary.curedIncr = int(obj['curedIncr'])
        outsideSummary.deadIncr = int(obj['deadIncr'])
        outsideSummary.updatedTime = datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S')
        return outsideSummary



    # 创建Dataservice对象
    ds = DataService(dsin)
    outsideSummary=fetch_outside_summary(obj)
    ds.db.save_outsideSummary_datas(outsideSummary)
    
ds=['localhost','root','20Z00t10x28_my','covid19']
OutsideSummary(ds)


+++ [MyDB] delete from outsideSummary_realtime_datas
+++ save_outsideSummary_datas, data len: 1
+++ save_outsideSummary_datas is over.
